In [1]:
import os
import glob
import pandas as pd

#import numpy as np
import bokeh
#import bokeh.plotting
#import bokeh.palettes
#from bokeh.transform import jitter
#from bokeh.models import HoverTool
from bokeh.models import Range1d
#from bokeh.models import ColumnDataSource
#from bokeh.palettes import Spectral6
#from bokeh.layouts import row
#bokeh.io.output_notebook()

import seaborn as sns
import matplotlib

from scipy import stats

#import math


import paqa_level_utils as paqa

Loading BokehJS ...

paqa_level_utils loaded correctfully


In [1]:
data_path = ["Y:/Lorenzo/Microscopy Data/Nikon widefield/2021/20210323", "Y:/Lorenzo/Microscopy Data/Nikon widefield/2021/20210324", "Y:/Lorenzo/Microscopy Data/Nikon widefield/2021/20210520"]
#data_path = 'C:/Users/lorenzo/Desktop/BacStalk_Data'
working_path = "C:/Users/lorenzo/Desktop/git/PhD_codes/Mechanosensation/Python_code/Motor_localization_analysis/"

os.chdir(working_path)
new_dir = "Data_PaQa_levels_pilBT_WT\\"
working_data_path = working_path + new_dir
if not os.path.exists(new_dir):
    os.mkdir(new_dir)
    

extension = 'csv'
list_csv = []
for path in data_path:
    os.chdir(path)
    for root, dirs, files in os.walk(path, topdown=False):
        for name in files:
            if extension in name:
                list_csv.append(os.path.join(root, name))

for file in list_csv:
    df_temp = pd.read_csv(file, sep=',', na_values='*')
    split_name=file.rsplit('Data_',2)[1].rsplit('_',100)
    #print(file)
    #print(split_name)
    file_name = file.rsplit("\\",2)[2]
    df_temp['Strain'] = split_name[0]
    if 'sol' in file:
        df_temp['Growth']='Solid'
    else:
        df_temp['Growth']='Liquid'
    df_temp['Bio_Rep']=int(split_name[len(split_name)-1].rsplit('BR=', 2)[1].rsplit('.',2)[0])
    df_temp.to_csv(working_data_path + 'enhanced_' + file_name, index = None, header=True)
    list_enhanced_csv = []

    
for root, dirs, files in os.walk(working_data_path, topdown=False):
    for name in files:
        if extension in name:
            list_enhanced_csv.append(os.path.join(root, name))

combined_csv = pd.concat([pd.read_csv(f) for f in list_enhanced_csv ], sort=False)
os.chdir(working_path)
combined_csv.to_csv( "SummaryPaQa-Copy_with_pilBT_WT.csv", index=False, encoding='utf-8-sig')

NameError: name 'os' is not defined

In [2]:
df_long = pd.read_csv('SummaryPaQa-Copy_with_pilBT_WT.csv', sep=',', na_values='*')
df_long['PaQa_ratio']=df_long['MeanCellIntensity_PaQa']/df_long['MeanCellIntensity_RFP']
lengths = df_long.groupby(['Strain', 'Growth', 'Bio_Rep'])['CellLength'].median().to_frame().reset_index()
l_max=lengths.CellLength.max()
df=df_long.loc[(df_long['CellLength'] <= l_max)].copy()
df_long.head()
print(df_long.Strain.unique())

['fliC-' 'pilA-T8V-FliC-' 'pilA-T8V' 'pilB-pilA-T8V' 'pilT-pilA-T8V' 'WT']


In [3]:
#param='MeanCellIntensity_mNeonGreen'
param='PaQa_ratio'
    
[means, stds, indexes, labels] = paqa.getDFStats(df_long, param)

#stds = df.groupby(['Strain', 'Growth', 'Labels', 'Bio_Rep'])[param].std().to_frame().reset_index()
#df.to_csv( "DataSet.csv", index=False, encoding='utf-8-sig')
#means_pilT
means.head(10)

Strain  Growth  Labels  Bio_Rep  PaQa_ratio    N
0        WT  Liquid    10.5        1    0.778103  577
1        WT  Liquid    10.5        2    0.794290  386
2        WT  Liquid    10.5        3    0.773331  350
3        WT   Solid    11.5        1    1.949414  538
4     fliC-  Liquid     0.5        1    0.442682  301
5     fliC-  Liquid     0.5        2    1.236610  500
6     fliC-  Liquid     0.5        3    1.205840  780
7     fliC-   Solid     1.5        1    1.722047  779
8  pilA-T8V  Liquid     4.5        1    1.494161  691
9  pilA-T8V  Liquid     4.5        2    1.757941  602

In [4]:
colors = bokeh.palettes.d3['Category20'][20]*3
growth=['Liquid', 'Solid']

p1, me1 = paqa.plottingData(df_long, means, 'fliC-', ['WT', 'pilA-T8V', 'pilA-T8V-FliC-', 'pilB-pilA-T8V', 'pilT-pilA-T8V'], [], growth, param, colors, 'linear', '',True)
#p1, me1 = paqa.plottingData(df_long, means, 'fliC-lolo', ['WT-Px2','WT-lolo','WT-alex','fliC-', 'WT', '764-fliC-', 'pilAt8v-fliC-', 'pilAT8V', 'pilB-fliC-T8V', 'pilT-fliC-T8V'], ['pilH-fliC-','cpdA-fliC-', 'pilH-cpdA-fliC-', 'pilG-cpdA-fliC-', 'pilG-fliC-', 'cyaB-fliC-', 'pilG-cyaB-fliC-', 'pilH-cyaB-fliC-', 'pilT-pilA-fliC-', 'pilH-', 'pilTU-fliC-'], growth, param, colors, 'linear', '')
#p2, me2 = plottingData(df_long, means, 'fliC-lolo', ['pilH-fliC-','cpdA-fliC-', 'pilG-fliC-', 'cyaB-fliC-', 'pilTU-fliC-', 'pilG-cyaB-fliC-', 'pilH-cyaB-fliC-', 'pilG-cpdA-fliC-', 'pilH-cpdA-fliC-'], ['WT-Px2','WT-lolo','WT-alex','fliC-','pilAT8V', 'pilB-fliC-T8V', 'pilT-fliC-T8V', 'pilT-pilA-fliC-', 'pilH-'], growth, param, colors, 'log', '')
p1.xgrid.grid_line_color = None
p1.ygrid.grid_line_color = None
p1.yaxis.minor_tick_line_color = None
p1.xaxis.minor_tick_line_color = None
p1.x_range=Range1d(0,14)
p1.output_backend = 'webgl'#'svg'
bokeh.io.show(p1)
#bokeh.io.show(row(p1,p2))

fliC- Liquid mean=[0.442682   1.23660953 1.20584016]
fliC- Solid mean=[1.72204685]
fliC- Solid fold increase=[1.79060823]
WT Liquid mean=[0.77810264 0.7942896  0.77333142]
WT Liquid fold increase=[0.80908193 0.82591336 0.80412075]
WT Solid mean=[1.94941432]
WT Solid fold increase=[2.02702808]
pilA-T8V Liquid mean=[1.49416112 1.75794064 1.66528399]
pilA-T8V Liquid fold increase=[1.55364948 1.82793109 1.73158543]
pilA-T8V Solid mean=[4.5389757]
pilA-T8V Solid fold increase=[4.71968997]
pilA-T8V-FliC- Liquid mean=[0.95716312 1.51971425 2.45383417]
pilA-T8V-FliC- Liquid fold increase=[0.99527151 1.58021999 2.55153085]
pilA-T8V-FliC- Solid mean=[3.91930455]
pilA-T8V-FliC- Solid fold increase=[4.07534731]
pilB-pilA-T8V Liquid mean=[0.43754033 0.42414801 0.49216442]
pilB-pilA-T8V Liquid fold increase=[0.45496051 0.44103499 0.5117594 ]
pilB-pilA-T8V Solid mean=[2.39604184 2.43614675 2.51070677]
pilB-pilA-T8V Solid fold increase=[2.49143758 2.53313923 2.61066777]
pilT-pilA-T8V Liquid mean=[0.34

In [4]:
colors = bokeh.palettes.d3['Category20'][20]*3
growth='Liquid'

p1, me1 = paqa.plottingData(df_long, means, 'fliC-', ['WT', 'pilA-T8V', 'pilA-T8V-FliC-', 'pilB-pilA-T8V', 'pilT-pilA-T8V'], [], growth, param, colors, 'linear', '',True)
#p1, me1 = paqa.plottingData(df_long, means, 'fliC-lolo', ['WT-Px2','WT-lolo','WT-alex','fliC-', 'WT', '764-fliC-', 'pilAt8v-fliC-', 'pilAT8V', 'pilB-fliC-T8V', 'pilT-fliC-T8V'], ['pilH-fliC-','cpdA-fliC-', 'pilH-cpdA-fliC-', 'pilG-cpdA-fliC-', 'pilG-fliC-', 'cyaB-fliC-', 'pilG-cyaB-fliC-', 'pilH-cyaB-fliC-', 'pilT-pilA-fliC-', 'pilH-', 'pilTU-fliC-'], growth, param, colors, 'linear', '')
#p2, me2 = plottingData(df_long, means, 'fliC-lolo', ['pilH-fliC-','cpdA-fliC-', 'pilG-fliC-', 'cyaB-fliC-', 'pilTU-fliC-', 'pilG-cyaB-fliC-', 'pilH-cyaB-fliC-', 'pilG-cpdA-fliC-', 'pilH-cpdA-fliC-'], ['WT-Px2','WT-lolo','WT-alex','fliC-','pilAT8V', 'pilB-fliC-T8V', 'pilT-fliC-T8V', 'pilT-pilA-fliC-', 'pilH-'], growth, param, colors, 'log', '')
p1.xgrid.grid_line_color = None
p1.ygrid.grid_line_color = None
p1.yaxis.minor_tick_line_color = None
p1.xaxis.minor_tick_line_color = None
p1.x_range=Range1d(0,9)
p1.output_backend = 'webgl'#'svg'
bokeh.io.show(p1)
#bokeh.io.show(row(p1,p2))
print(colors)

Not a list
fliC- Liquid mean=[0.442682   1.23660953 1.20584016]
fliC- Solid mean=[1.72204685]
fliC- Solid fold increase=[1.79060823]
WT mean=[0.77810264 0.7942896  0.77333142]
WT fold increase=[0.80908193 0.82591336 0.80412075]
pilA-T8V mean=[1.49416112 1.75794064 1.66528399]
pilA-T8V fold increase=[1.55364948 1.82793109 1.73158543]
pilA-T8V-FliC- mean=[0.95716312 1.51971425 2.45383417]
pilA-T8V-FliC- fold increase=[0.99527151 1.58021999 2.55153085]
pilB-pilA-T8V mean=[0.43754033 0.42414801 0.49216442]
pilB-pilA-T8V fold increase=[0.45496051 0.44103499 0.5117594 ]
pilT-pilA-T8V mean=[0.34803136 0.41560032 0.44916105]
pilT-pilA-T8V fold increase=[0.36188784 0.43214698 0.46704389]
12
10
8
6
4
1
0


('#1f77b4', '#aec7e8', '#ff7f0e', '#ffbb78', '#2ca02c', '#98df8a', '#d62728', '#ff9896', '#9467bd', '#c5b0d5', '#8c564b', '#c49c94', '#e377c2', '#f7b6d2', '#7f7f7f', '#c7c7c7', '#bcbd22', '#dbdb8d', '#17becf', '#9edae5', '#1f77b4', '#aec7e8', '#ff7f0e', '#ffbb78', '#2ca02c', '#98df8a', '#d62728', '#ff9896', '#9467bd', '#c5b0d5', '#8c564b', '#c49c94', '#e377c2', '#f7b6d2', '#7f7f7f', '#c7c7c7', '#bcbd22', '#dbdb8d', '#17becf', '#9edae5', '#1f77b4', '#aec7e8', '#ff7f0e', '#ffbb78', '#2ca02c', '#98df8a', '#d62728', '#ff9896', '#9467bd', '#c5b0d5', '#8c564b', '#c49c94', '#e377c2', '#f7b6d2', '#7f7f7f', '#c7c7c7', '#bcbd22', '#dbdb8d', '#17becf', '#9edae5')


In [6]:
colors = bokeh.palettes.d3['Category20'][20]*3
growth='Liquid'

p1, me1, source = paqa.plottingDataMeans(df_long, means, 'fliC-lolo', ['764-fliC-', 'pilAt8v-fliC-', 'pilAT8V'], ['WT-Px2', 'pilB-fliC-T8V', 'pilT-fliC-T8V','WT-lolo','WT-alex','fliC-', 'WT','pilH-fliC-','cpdA-fliC-', 'pilH-cpdA-fliC-', 'pilG-cpdA-fliC-', 'pilG-fliC-', 'cyaB-fliC-', 'pilG-cyaB-fliC-', 'pilH-cyaB-fliC-', 'pilT-pilA-fliC-', 'pilH-', 'pilTU-fliC-'], growth, param, colors, 'linear', '')
#p2, me2 = plottingData(df_long, means, 'fliC-lolo', ['pilH-fliC-','cpdA-fliC-', 'pilG-fliC-', 'cyaB-fliC-', 'pilTU-fliC-', 'pilG-cyaB-fliC-', 'pilH-cyaB-fliC-', 'pilG-cpdA-fliC-', 'pilH-cpdA-fliC-'], ['WT-Px2','WT-lolo','WT-alex','fliC-','pilAT8V', 'pilB-fliC-T8V', 'pilT-fliC-T8V', 'pilT-pilA-fliC-', 'pilH-'], growth, param, colors, 'log', '')
p1.xgrid.grid_line_color = None
p1.ygrid.grid_line_color = None
p1.xaxis.minor_tick_line_color = None
p1.xaxis.minor_tick_line_color = 'grey'
p1.x_range=Range1d(0,21)
p1.output_backend = 'svg'
bokeh.io.show(p1)

Not a list
fliC-lolo Liquid mean=[]
fliC-lolo Solid mean=[]
fliC-lolo Solid fold increase=[]
764-fliC- mean=[]
764-fliC- fold increase=[]
pilAt8v-fliC- mean=[]
pilAt8v-fliC- fold increase=[]
pilAT8V mean=[]
pilAT8V fold increase=[]


IndexError: list assignment index out of range

In [15]:
p = bokeh.plotting.figure(
    width=500, 
    height=300,  
    y_axis_type='linear',
    y_axis_label = 'fold increase',
    title= 'PaQa levels',
    y_range=Range1d(0, 5),
    x_range=source.data['names']
)

p.vbar(x='names', top='y_values', width=0.5, color='color', source=source)
p.output_backend = 'svg'
p.xgrid.visible = False
p.ygrid.visible = True
#p.xaxis.minor_tick_line_color = None
p.xaxis.major_label_orientation = math.pi/4
p.yaxis.minor_tick_line_color = None
bokeh.io.show(p)

In [6]:
p3 = plottingDataUnique(df_long, means, 'fliC-lolo', ['pilH-fliC-','cpdA-fliC-', 'pilG-fliC-', 'cyaB-fliC-', 'pilTU-fliC-', 'pilG-cyaB-fliC-', 'pilH-cyaB-fliC-', 'pilG-cpdA-fliC-', 'pilH-cpdA-fliC-'], ['WT-Px2','WT-lolo','WT-alex','fliC-','pilAT8V', 'pilB-fliC-T8V', 'pilT-fliC-T8V', 'pilT-pilA-fliC-', 'pilH-'], 'Liquid', param, colors, 'linear', '')
bokeh.io.show(p3)

TypeError: unsupported operand type(s) for /: 'list' and 'list'

In [7]:
p4, means3 = plottingData(df_long, means, 'fliC-lolo', ['pilH-fliC-','cpdA-fliC-', 'pilH-cpdA-fliC-', 'pilG-fliC-', 'cyaB-fliC-', 'pilG-cyaB-fliC-', 'pilH-cyaB-fliC-', 'pilG-cpdA-fliC-', 'pilT-pilA-fliC-'], ['pilH-','WT', 'pilAT8V', 'pilB-fliC-T8V', 'pilT-fliC-T8V','WT-Px2','WT-lolo','WT-alex','fliC-'], 'Liquid', param, colors, 'linear', '')
bokeh.io.show(p4)
means3.head(100)

Not a list
fliC-lolo Liquid mean=[0.71876818 0.34404673 0.83255467]
fliC-lolo Solid mean=[2.01878754 2.53624806 2.47896103]
fliC-lolo Solid fold increase=[3.19534653 4.01438551 3.92371133]
pilH-fliC- mean=[10.12544536  8.74868479  9.05803649]
pilH-fliC- fold increase=[16.02660312 13.84745993 14.33710328]
cpdA-fliC- mean=[8.89190707 8.48713803 9.10609987]
cpdA-fliC- fold increase=[14.07415285 13.43348247 14.41317822]
pilH-cpdA-fliC- mean=[10.93336413 12.14036353  9.05318959]
pilH-cpdA-fliC- fold increase=[17.30538079 19.21582518 14.32943158]
pilG-fliC- mean=[0.29296532 0.31665676 0.26532618]
pilG-fliC- fold increase=[0.4637069  0.50120582 0.41995953]
cyaB-fliC- mean=[0.29359093 0.28100342 0.28081422]
cyaB-fliC- fold increase=[0.46469713 0.44477356 0.44447408]
pilG-cyaB-fliC- mean=[0.35696244 0.3246434  0.32256305]
pilG-cyaB-fliC- fold increase=[0.56500185 0.51384712 0.51055432]
pilH-cyaB-fliC- mean=[0.36488302 0.34146138 0.3469086 ]
pilH-cyaB-fliC- fold increase=[0.57753858 0.5404667  0

Strain  Growth  Labels  Bio_Rep  PaQa_ratio     N
7        cpdA-fliC-  Liquid     3.5        1   14.074153   346
8        cpdA-fliC-  Liquid     3.5        2   13.433482   595
9        cpdA-fliC-  Liquid     3.5        3   14.413178   937
11       cyaB-fliC-  Liquid     6.5        1    0.464697   253
12       cyaB-fliC-  Liquid     6.5        2    0.444774   530
13       cyaB-fliC-  Liquid     6.5        3    0.444474   559
19        fliC-lolo  Liquid     0.5        1    1.137670   353
20        fliC-lolo  Liquid     0.5        2    0.544559   398
21        fliC-lolo  Liquid     0.5        3    1.317771   581
22        fliC-lolo   Solid     1.5        1    2.808677   613
23        fliC-lolo   Solid     1.5        2    7.371813   648
24        fliC-lolo   Solid     1.5        3    2.977535   438
27  pilG-cpdA-fliC-  Liquid     9.5        1   11.665424   150
28  pilG-cpdA-fliC-  Liquid     9.5        2    4.083096   606
29  pilG-cpdA-fliC-  Liquid     9.5        3    4.822818   495
30  pilG-cpdA-fliC-  Liquid     9.5        4    4.711407   755
31  pilG-cpdA-fliC-  Liquid     9.5        5    4.334226   333
32  pilG-cyaB-fliC-  Liquid     7.5        1    0.565002   249
33  pilG-cyaB-fliC-  Liquid     7.5        2    0.513847   966
34  pilG-cyaB-fliC-  Liquid     7.5        3    0.510554   613
35       pilG-fliC-  Liquid     5.5        1    0.463707   155
36       pilG-fliC-  Liquid     5.5        2    0.501206   465
37       pilG-fliC-  Liquid     5.5        3    0.419960   547
40  pilH-cpdA-fliC-  Liquid     4.5        1   17.305381   434
41  pilH-cpdA-fliC-  Liquid     4.5        2   19.215825   876
42  pilH-cpdA-fliC-  Liquid     4.5        3   14.329432   657
43  pilH-cyaB-fliC-  Liquid     8.5        1    0.577539   129
44  pilH-cyaB-fliC-  Liquid     8.5        2    0.540467   960
45  pilH-cyaB-fliC-  Liquid     8.5        3    0.549089   862
46       pilH-fliC-  Liquid     2.5        1   16.026603   187
47       pilH-fliC-  Liquid     2.5        2   13.847460   838
48       pilH-fliC-  Liquid     2.5        3   14.337103   703
51  pilT-pilA-fliC-  Liquid    10.5        1    0.524035   150
53      pilTU-fliC-  Liquid    30.5        2    0.510108   608
54      pilTU-fliC-  Liquid    30.5        3    0.581639  1492
55      pilTU-fliC-  Liquid    30.5        4    0.540132   505